In [1]:
import re
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import string
import re
import emoji
import nltk
import warnings
warnings.filterwarnings('ignore', category=DeprecationWarning)
import numpy as np
import nltk
from sklearn.model_selection import train_test_split

%matplotlib inline

In [14]:
choni_csv = pd.read_csv('bughead_new.csv.csv');
choni_csv.head(10)

tweets  quote_status language  \
0  RT @nabrinas: a thread of every barchie kiss 🥰...         False       en   
1  RT @barchie_gifs: The forehead touch 🥺\r\n[5.0...         False       en   
2  RT @bossbex1: Betty's face when she's "disappo...         False       en   
3  this is going to be barchie when glenn and ver...          True       en   
4    being a barchie girl is a marginalized identity         False       en   
5  RT @SuperheroTVcom: VOTE: Riverdale Time Jump!...         False       en   
6  RT @laylasblair: #BARCHIE : maybe i can distra...         False       en   
7  FORGOT THERE WAS MORE THAN ONE BARCHIE KISS IN...         False       en   
8                       barchie gives me butterflies         False       en   
9      @JuliDG Delena, Leyton and Barchie my otps ♥️         False       en   

   favorite_count  retweet_count                 time                   id  \
0               0             69  2021-02-27 05:13:08  1365530382691487751   
1               0             40  2021-02-27 05:12:48  1365530301288640512   
2               0             10  2021-02-27 05:09:31  1365529473567760386   
3               0              0  2021-02-27 05:09:28  1365529460213092353   
4               0              0  2021-02-27 05:08:49  1365529297822179329   
5               0            557  2021-02-27 05:07:56  1365529076820307969   
6               0             36  2021-02-27 05:07:36  1365528991080189953   
7               0              0  2021-02-27 05:06:22  1365528679351205889   
8               1              0  2021-02-27 05:03:50  1365528042270060544   
9               0              0  2021-02-27 05:03:03  1365527845255090179   

                                      processed_text  \
0             ['thread', 'every', 'barchie', 'kiss']   
1  ['forehead', 'touch', '5', '06', 'chapter', 'e...   
2  ['betty', 'face', 'disappointed', 'jughead', '...   
3  ['going', 'barchie', 'glenn', 'veronica', 'com...   
4    ['barchie', 'girl', 'marginalized', 'identity']   
5  ['vote', 'riverdale', 'time', 'jump', 'archie'...   
6  ['barchie', 'maybe', 'distract', 'sexual', 'te...   
7    ['forgot', 'one', 'barchie', 'kiss', 'episode']   
8                ['barchie', 'gives', 'butterflies']   
9            ['delena', 'leyton', 'barchie', 'otps']   

                                      cleaned_tweets  
0                          thread every barchie kiss  
1  forehead touch 5 06 chapter eighty two back sc...  
2       betty face disappointed jughead home barchie  
3          going barchie glenn veronica come picture  
4                 barchie girl marginalized identity  
5  vote riverdale time jump archie amp betty like...  
6              barchie maybe distract sexual tension  
7                    forgot one barchie kiss episode  
8                          barchie gives butterflies  
9                         delena leyton barchie otps

In [15]:
# Rule-based approach
posTokens = ["love", "sexy", "hot", "good", "perfect", "beautiful", "like", "sexi", "sexxy", "luv", "fav", "favorite", "riot", 
             "endgame", "great", "happy"]
negTokens = ["beef", "choke", "fail", "barf", "hate", "yasss", "trash", "disgusting", "quit", "give up", "boring", "boring", 
             "ugly", "dumb", "hatred", "tsk", "...", "bad"]
sentimentPos = []
sentimentNeg = []
sentimentNeu = []

emoteToken = {
  ":smile:":"positive", ":simple_smile:":"positive", ":laughing:":"positive", ":blush:":"positive", ":heart_eyes:":"positive", 
    ":smirk:":"positive", ":starstruck:":"positive", ":kissing_heart:":"positive", ":kissing_closed_eyes:":"positive", 
    ":flushed:":"positive", ":relieved":"positive", ":satisfied:":"positive", ":grin:":"positive", ":wink:":"positive",
    ":stuck_out_tongue_winking_eye:":"neutral", ":stuck_out_tongue_closed_eyes:":"negative", ":grinning:":"positive",
    ":kissing:":"positive", ":kissing_smiling_eyes:":"positive", ":stuck_out_tongue:":"positive", ":sleeping:":"negative",
    ":worried:":"negative", ":frowning:":"negative", ":anguished:":"negative", ":open_mouth:":"neutral", 
    ":grimacing:":"negative", ":confused:":"neutral", ":hushed:":"neutral", ":expressionless:":"negative", 
    ":unamused:":"negative", ":sweat_smile:":"positive", ":sweat:":"negative", ":disappointed_relieved:":"negative",
    ":disappointed:":"negative", ":sob:":"negative", ":joy:":"positive", ":smiling_imp:":"positive", ":heart:":"positive",
    ":cloud_with_rain:":"positive", ":loudly crying face:":"positive", ":thinking_face:":"neutral", 
    ":smiling_face_with_halo:":"positive", ":face_with_rolling_eyes:":"negative", ":revolving_hearts:":"positive",
    ":relieved_face:":"positive", ":face_with_tears_of_joy:":"positive", ":heart_with_arrow:":"positive",
    ":sparkling_heart:":"positive", ":heart_with_ribbon:":"positive", ":pleading_face:":"positive",
    ":sparkles:":"positive", ":purple_heart:":"positive", ":unicorn:":"positive", ":broken_heart:":"positive",
    ":pensive_face:":"neutral", ":smirking face:":"positive", ":confused_face:":"neutral",
    ":smiling_face_with_hearts:":"positive", ":sleepy:":"negative",":blue_heart:":"positive",":fire:":"positive",
    ":hankey:":"negative", 
}

# Keep track of sentiment value
posValue = 0
negValue = 0
neutralValue = 0

# Keep track of cleaned tweets
cleanedTweets = []

In [16]:
for column_name in choni_csv:
    print(column_name)

tweets
quote_status
language
favorite_count
retweet_count
time
id
processed_text
cleaned_tweets


In [17]:
for column_name, item in choni_csv.iteritems():
    if column_name == 'tweets':
        print(item)
        print('------')

0       RT @nabrinas: a thread of every barchie kiss 🥰...
1       RT @barchie_gifs: The forehead touch 🥺\r\n[5.0...
2       RT @bossbex1: Betty's face when she's "disappo...
3       this is going to be barchie when glenn and ver...
4         being a barchie girl is a marginalized identity
                              ...                        
5886    starting to think me liking barchie somehow is...
5887    @barchieslovee Ye that's what I was saying his...
5888                           @azalben we need barchie🔥🔥
5889    @azalben this is definitely barchie related an...
5890     @jalebhizzie ME TOOOoo, but I still ship Barchie
Name: tweets, Length: 5891, dtype: object
------


In [18]:
def normalize_Text(text):
    print('---[START]text before modifying:---')
    print(text)
    textModified = text.lower()
    textModified = emoji.demojize(textModified)
    print('---Emoji modified text---')
    print(textModified)
    textModified = re.sub("@[A-Za-z0-9]+","", textModified) #Remove @ sign
    textModified = re.sub(r"(?:\@|http?\://|https?\://|www)\S+", "", textModified) #Remove http links
    textModified = textModified.replace("#", "").replace("_", " ") #Remove hashtag sign but keep the text
    print("---Removed Unnecesary pieces---")
    print(textModified)
    print('---[END]---')
    return textModified
    
def sentiment_by_rules(text):
    # First clean the text
    global posValue;
    global negValue;
    global neutralValue;
    cleanedText = normalize_Text(text)
    # calculate emotes before splitting keys as its hard to do a key comparison with string split
    for key in emoteToken:
        if key in text:
            if emoteToken[key] == 'positive':
                posValue = posValue + 1
            elif emoteToken[key] == 'negative':
                negValue = negValue + 1
            else:
                neutralValue = neutralValue + 1
    cleanedTweets.append(cleanedText)
    # split string so its easier to do token comparison
    textSplit = cleanedText.split()
    print("Text Split:")
    print(textSplit)
    for x in textSplit:
        if ':' in x :
            #if theres a colon then that means it has an emote so ignore adding double pos or neg or neu values
            pass
        elif any(ele for ele in posTokens if(ele in x)):
            posValue = posValue + 1
        elif any(ele for ele in negTokens if(ele in x)):
            negValue = negValue + 1
        else :
            neutralValue = neutralValue + 1
    
    # If neutral value is greater than 3 times the sum of posValue and negValue than have a consistant normalizer of div 3
    # so if pos and neg are 2 each but neutral is 12 or more divide it by 3 to make values a little more consistent. Ignore
    # this if theres no posValue or negValue as that should be a neutral statement then
    if posValue != 0 and negValue != 0 and neutralValue > ((posValue + negValue) * 3):
        neutralValue = neutralValue / 3
    
    total = posValue + negValue + neutralValue
    
    if total != 0:
        sentimentPos.append(float(posValue / total))
        sentimentNeg.append(float(negValue / total))
        sentimentNeu.append(float(neutralValue / total))
    else:
        sentimentPos.append(0)
        sentimentNeg.append(0)
        sentimentNeu.append(0)
    
    posValue = 0
    negValue = 0
    neutralValue = 0
    

In [19]:
for ind in choni_csv.index:
    sentiment_by_rules(choni_csv['tweets'][ind])

---[START]text before modifying:---
RT @nabrinas: a thread of every barchie kiss 🥰
 https://t.co/H8p1UDdQdZ
---Emoji modified text---
rt @nabrinas: a thread of every barchie kiss :smiling_face_with_hearts:
 https://t.co/h8p1uddqdz
---Removed Unnecesary pieces---
rt : a thread of every barchie kiss :smiling face with hearts:
 
---[END]---
Text Split:
['rt', ':', 'a', 'thread', 'of', 'every', 'barchie', 'kiss', ':smiling', 'face', 'with', 'hearts:']
---[START]text before modifying:---
RT @barchie_gifs: The forehead touch 🥺
[5.06 - Chapter Eighty-Two: Back To School]
@lilireinhart @RiverdaleWriter @WriterRAS
#Barchie #Rive…
---Emoji modified text---
rt @barchie_gifs: the forehead touch :pleading_face:
[5.06 - chapter eighty-two: back to school]
@lilireinhart @riverdalewriter @writerras
#barchie #rive…
---Removed Unnecesary pieces---
rt  gifs: the forehead touch :pleading face:
[5.06 - chapter eighty-two: back to school]
  
barchie rive…
---[END]---
Text Split:
['rt', 'gifs:', 'the', 'fore

@mikhailosbff i don’t like betty but barchie kinda cute…
---Emoji modified text---
@mikhailosbff i don’t like betty but barchie kinda cute…
---Removed Unnecesary pieces---
 i don’t like betty but barchie kinda cute…
---[END]---
Text Split:
['i', 'don’t', 'like', 'betty', 'but', 'barchie', 'kinda', 'cute…']
---[START]text before modifying:---
daily reminder that this account is 100% a bughead and varchie account not barchie at all
---Emoji modified text---
daily reminder that this account is 100% a bughead and varchie account not barchie at all
---Removed Unnecesary pieces---
daily reminder that this account is 100% a bughead and varchie account not barchie at all
---[END]---
Text Split:
['daily', 'reminder', 'that', 'this', 'account', 'is', '100%', 'a', 'bughead', 'and', 'varchie', 'account', 'not', 'barchie', 'at', 'all']
---[START]text before modifying:---
RT @barchanted: I will be voting for Barchie, Choni, and Falice. Who's with me? 😇
---Emoji modified text---
rt @barchanted: i wil

  6666  support ok but did you see how betty ended barchie in s4? or maybe now in s5 how betty tells archie how shes worried and he just answer with an "oh it sucks maybe i can distract you tonight" or something like that? but these are opinions so the fact is just that we think differently lol
---[END]---
Text Split:
['6666', 'support', 'ok', 'but', 'did', 'you', 'see', 'how', 'betty', 'ended', 'barchie', 'in', 's4?', 'or', 'maybe', 'now', 'in', 's5', 'how', 'betty', 'tells', 'archie', 'how', 'shes', 'worried', 'and', 'he', 'just', 'answer', 'with', 'an', '"oh', 'it', 'sucks', 'maybe', 'i', 'can', 'distract', 'you', 'tonight"', 'or', 'something', 'like', 'that?', 'but', 'these', 'are', 'opinions', 'so', 'the', 'fact', 'is', 'just', 'that', 'we', 'think', 'differently', 'lol']
---[START]text before modifying:---
RT @barchiecheated: @CW_Riverdale YESSIR
https://t.co/rBhFzrwcS5
---Emoji modified text---
rt @barchiecheated: @cw_riverdale yessir
https://t.co/rbhfzrwcs5
---Removed Unnecesar

---Emoji modified text---
@bjrchies when is the remake of barchie to play date:man_standing::man_standing: https://t.co/lgy23kzqjk
---Removed Unnecesary pieces---
 when is the remake of barchie to play date:man standing::man standing: 
---[END]---
Text Split:
['when', 'is', 'the', 'remake', 'of', 'barchie', 'to', 'play', 'date:man', 'standing::man', 'standing:']
---[START]text before modifying:---
Some people in the barchie fandom is snowbarry shippers. If you see me not following or talking to y'all. That is why. https://t.co/woGmEanPhb
---Emoji modified text---
some people in the barchie fandom is snowbarry shippers. if you see me not following or talking to y'all. that is why. https://t.co/wogmeanphb
---Removed Unnecesary pieces---
some people in the barchie fandom is snowbarry shippers. if you see me not following or talking to y'all. that is why. 
---[END]---
Text Split:
['some', 'people', 'in', 'the', 'barchie', 'fandom', 'is', 'snowbarry', 'shippers.', 'if', 'you', 'see', 'me', 

---Removed Unnecesary pieces---
  yeah barchie endgame, we know!
---[END]---
Text Split:
['yeah', 'barchie', 'endgame,', 'we', 'know!']
---[START]text before modifying:---
@BarchieUpdates @RiverdaleWriter @WriterRAS @lilireinhart @TheCW When it comes to #Barchie, there's only one song I can think of. And yes, I am that old.
https://t.co/lQ6xDHTKex
---Emoji modified text---
@barchieupdates @riverdalewriter @writerras @lilireinhart @thecw when it comes to #barchie, there's only one song i can think of. and yes, i am that old.
https://t.co/lq6xdhtkex
---Removed Unnecesary pieces---
     when it comes to barchie, there's only one song i can think of. and yes, i am that old.

---[END]---
Text Split:
['when', 'it', 'comes', 'to', 'barchie,', "there's", 'only', 'one', 'song', 'i', 'can', 'think', 'of.', 'and', 'yes,', 'i', 'am', 'that', 'old.']
---[START]text before modifying:---
Oh I wonder why ... https://t.co/eID59FPFGA
---Emoji modified text---
oh i wonder why ... https://t.co/eid59fpfga


...

---Emoji modified text---
okay enough of this madness give me barchie:beating_heart: we only had one romantic barchie moment i need more!!
---Removed Unnecesary pieces---
okay enough of this madness give me barchie:beating heart: we only had one romantic barchie moment i need more!!
---[END]---
Text Split:
['okay', 'enough', 'of', 'this', 'madness', 'give', 'me', 'barchie:beating', 'heart:', 'we', 'only', 'had', 'one', 'romantic', 'barchie', 'moment', 'i', 'need', 'more!!']
---[START]text before modifying:---
The barchie scene mad me want to rip my eyes out🤢🤮
---Emoji modified text---
the barchie scene mad me want to rip my eyes out:nauseated_face::face_vomiting:
---Removed Unnecesary pieces---
the barchie scene mad me want to rip my eyes out:nauseated face::face vomiting:
---[END]---
Text Split:
['the', 'barchie', 'scene', 'mad', 'me', 'want', 'to', 'rip', 'my', 'eyes', 'out:nauseated', 'face::face', 'vomiting:']
---[START]text before modifying:---
RT @bjrchies: those who think barchi

---Emoji modified text---
me coming back to #riverdale because of #barchie like: https://t.co/bmrqfwib3e
---Removed Unnecesary pieces---
me coming back to riverdale because of barchie like: 
---[END]---
Text Split:
['me', 'coming', 'back', 'to', 'riverdale', 'because', 'of', 'barchie', 'like:']
---[START]text before modifying:---
i miss barchie hurry up
---Emoji modified text---
i miss barchie hurry up
---Removed Unnecesary pieces---
i miss barchie hurry up
---[END]---
Text Split:
['i', 'miss', 'barchie', 'hurry', 'up']
---[START]text before modifying:---
heating is one word for that! #Barchie #Riverdale https://t.co/gp6UFxtrmz
---Emoji modified text---
heating is one word for that! #barchie #riverdale https://t.co/gp6ufxtrmz
---Removed Unnecesary pieces---
heating is one word for that! barchie riverdale 
---[END]---
Text Split:
['heating', 'is', 'one', 'word', 'for', 'that!', 'barchie', 'riverdale']
---[START]text before modifying:---
@loreIaiqilmore barchie, that ship from love rosie

Barchie got fucked by the bell... 💀 #Riverdale
---Emoji modified text---
barchie got fucked by the bell... :skull: #riverdale
---Removed Unnecesary pieces---
barchie got fucked by the bell... :skull: riverdale
---[END]---
Text Split:
['barchie', 'got', 'fucked', 'by', 'the', 'bell...', ':skull:', 'riverdale']
---[START]text before modifying:---
These motherfuckers just interrupted Barchie car sex 🤬
---Emoji modified text---
these motherfuckers just interrupted barchie car sex :face_with_symbols_on_mouth:
---Removed Unnecesary pieces---
these motherfuckers just interrupted barchie car sex :face with symbols on mouth:
---[END]---
Text Split:
['these', 'motherfuckers', 'just', 'interrupted', 'barchie', 'car', 'sex', ':face', 'with', 'symbols', 'on', 'mouth:']
---[START]text before modifying:---
WHAT ARE THEY SO HOT FOR? #Riverdale #Barchie
---Emoji modified text---
what are they so hot for? #riverdale #barchie
---Removed Unnecesary pieces---
what are they so hot for? riverdale barchie
---

---Emoji modified text---
if i see any archie comics on here it’s an automatic retweet especially if it’s about barchie. my old ass just loves the comics so much :pleading_face::black_heart:
---Removed Unnecesary pieces---
if i see any archie comics on here it’s an automatic retweet especially if it’s about barchie. my old ass just loves the comics so much :pleading face::black heart:
---[END]---
Text Split:
['if', 'i', 'see', 'any', 'archie', 'comics', 'on', 'here', 'it’s', 'an', 'automatic', 'retweet', 'especially', 'if', 'it’s', 'about', 'barchie.', 'my', 'old', 'ass', 'just', 'loves', 'the', 'comics', 'so', 'much', ':pleading', 'face::black', 'heart:']
---[START]text before modifying:---
@RiverdaleWriter Excited for Barchie
https://t.co/EdH7cka65c
---Emoji modified text---
@riverdalewriter excited for barchie
https://t.co/edh7cka65c
---Removed Unnecesary pieces---
 excited for barchie

---[END]---
Text Split:
['excited', 'for', 'barchie']
---[START]text before modifying:---
#barchi

---Emoji modified text---
rt @barchanted: wait! so betty and archie looking at eachother and toni and archie looking at eachother happens in very close succession...…
---Removed Unnecesary pieces---
rt : wait! so betty and archie looking at eachother and toni and archie looking at eachother happens in very close succession...…
---[END]---
Text Split:
['rt', ':', 'wait!', 'so', 'betty', 'and', 'archie', 'looking', 'at', 'eachother', 'and', 'toni', 'and', 'archie', 'looking', 'at', 'eachother', 'happens', 'in', 'very', 'close', 'succession...…']
---[START]text before modifying:---
riverdale today im collecting my barchie fwb today
---Emoji modified text---
riverdale today im collecting my barchie fwb today
---Removed Unnecesary pieces---
riverdale today im collecting my barchie fwb today
---[END]---
Text Split:
['riverdale', 'today', 'im', 'collecting', 'my', 'barchie', 'fwb', 'today']
---[START]text before modifying:---
@barchie_gifs @lilireinhart @RiverdaleWriter @WriterRAS Lmao you th

In [20]:
choni_csv["cleaned_tweets"] = cleanedTweets
choni_csv["neg"] = sentimentPos
choni_csv["neu"] = sentimentNeg
choni_csv["pos"] = sentimentNeu
choni_csv["neg"] = choni_csv["neg"].astype(float)
choni_csv["neu"] = choni_csv["neu"].astype(float)
choni_csv["pos"] = choni_csv["pos"].astype(float)
choni_csv["neg"] = choni_csv["neg"].map('{:,.2f}'.format)
choni_csv["neu"] = choni_csv["neu"].map('{:,.2f}'.format)
choni_csv["pos"] = choni_csv["pos"].map('{:,.2f}'.format)
choni_csv.head(10)

tweets  quote_status language  \
0  RT @nabrinas: a thread of every barchie kiss 🥰...         False       en   
1  RT @barchie_gifs: The forehead touch 🥺\r\n[5.0...         False       en   
2  RT @bossbex1: Betty's face when she's "disappo...         False       en   
3  this is going to be barchie when glenn and ver...          True       en   
4    being a barchie girl is a marginalized identity         False       en   
5  RT @SuperheroTVcom: VOTE: Riverdale Time Jump!...         False       en   
6  RT @laylasblair: #BARCHIE : maybe i can distra...         False       en   
7  FORGOT THERE WAS MORE THAN ONE BARCHIE KISS IN...         False       en   
8                       barchie gives me butterflies         False       en   
9      @JuliDG Delena, Leyton and Barchie my otps ♥️         False       en   

   favorite_count  retweet_count                 time                   id  \
0               0             69  2021-02-27 05:13:08  1365530382691487751   
1               0             40  2021-02-27 05:12:48  1365530301288640512   
2               0             10  2021-02-27 05:09:31  1365529473567760386   
3               0              0  2021-02-27 05:09:28  1365529460213092353   
4               0              0  2021-02-27 05:08:49  1365529297822179329   
5               0            557  2021-02-27 05:07:56  1365529076820307969   
6               0             36  2021-02-27 05:07:36  1365528991080189953   
7               0              0  2021-02-27 05:06:22  1365528679351205889   
8               1              0  2021-02-27 05:03:50  1365528042270060544   
9               0              0  2021-02-27 05:03:03  1365527845255090179   

                                      processed_text  \
0             ['thread', 'every', 'barchie', 'kiss']   
1  ['forehead', 'touch', '5', '06', 'chapter', 'e...   
2  ['betty', 'face', 'disappointed', 'jughead', '...   
3  ['going', 'barchie', 'glenn', 'veronica', 'com...   
4    ['barchie', 'girl', 'marginalized', 'identity']   
5  ['vote', 'riverdale', 'time', 'jump', 'archie'...   
6  ['barchie', 'maybe', 'distract', 'sexual', 'te...   
7    ['forgot', 'one', 'barchie', 'kiss', 'episode']   
8                ['barchie', 'gives', 'butterflies']   
9            ['delena', 'leyton', 'barchie', 'otps']   

                                      cleaned_tweets   neg   neu   pos  
0  rt : a thread of every barchie kiss :smiling f...  0.00  0.00  1.00  
1  rt  gifs: the forehead touch :pleading face:\r...  0.00  0.00  1.00  
2  rt : betty's face when she's "disappointed" th...  0.00  0.00  1.00  
3  this is going to be barchie when glenn and ver...  0.00  0.00  1.00  
4    being a barchie girl is a marginalized identity  0.00  0.00  1.00  
5  rt : vote: riverdale time jump! \r\nretweet: a...  0.00  0.00  1.00  
6  rt : barchie : maybe i can distract you... *se...  0.00  0.11  0.89  
7  forgot there was more than one barchie kiss in...  0.00  0.00  1.00  
8                       barchie gives me butterflies  0.00  0.00  1.00  
9    delena, leyton and barchie my otps :heart suit:  0.00  0.00  1.00

In [21]:
# save in df
choni_csv.to_csv('bughead_new_rba.csv',index=False)